# Position Reconstruction for XeBRA - Neural Networks

**Status:** August 2019

Position reconstruction for XeBRA using a feedforward neural network with Keras.
Purpose of this notebook: Keras Hyperparameter Tuning using Hyperas.

In [ ]:
#############################################
## Use Google Colab:
#############################################
b_GC = False # True or False

if b_GC == True:
    !pip install hyperas
    !pip install hyperopt

In [1]:
#############################################
## Imports:
#############################################

from __future__ import print_function
import numpy as np

from hyperopt import Trials, STATUS_OK, tpe
from keras.datasets import mnist
from keras.layers.core import Dense, Dropout, Activation
from keras.models import Sequential
from keras.utils import np_utils
from keras.optimizers import SGD,Adam

from hyperas import optim
from hyperas.distributions import choice, uniform

import glob
import uproot
import pandas as pd

Using TensorFlow backend.


In [2]:
#############################################
## Preparing the Data
#############################################

def data():
    """
    Data providing function:

    This function is separated from create_model() so that hyperopt
    won't reload data for each evaluation run.
    """

    ## Selection of file(s) to be used:
    filename_list = glob.glob("/media/alex/TOSHIBA EXT/Simulation_Data/LCE/optPhot_S2_1.0e+05_pmtGap4.5_RPTFE0.95_LXeAbs100_Tmesh0.89770509_writeEmptyFalse_nop_1.0e+04_*.root")                
    file_split_train = 0.9 # fraction of file used for training
    
    ## Import as pandas dataframes
    branches= ['xp_pri','yp_pri','zp_pri','ntpmthits','pmthits'] # Be careful that the branches are also initilized in _chunk_collect
    import concurrent.futures
    executor = concurrent.futures.ThreadPoolExecutor(8)
    _chunk_collect = pd.DataFrame({'xp_pri' : [],'yp_pri' : [],'zp_pri' : [], 'ntpmthits' : [],'pmthits' : []}) # Initialize empty data frame
    for _chunk in uproot.iterate(filename_list, "events/events",branches, entrysteps=100000, 
                                           outputtype=pd.DataFrame, executor=executor):
        _chunk.columns=branches
        _chunk_collect=_chunk_collect.append(_chunk)

    ## Normalize to hits fractions
    _chunk_collect['pmthits'] = (_chunk_collect['pmthits'] / _chunk_collect['ntpmthits'])

    ## Separate hits for individual PMTs
    ## Takes a while to calculate...
    for i in range(1,8):
        _chunk_collect['pmthits_'+str(i)] = pd.Series([tupl[i] for tupl in np.asarray(_chunk_collect['pmthits'])], index=_chunk_collect.index)

    _chunk_collect = _chunk_collect.drop(columns=['pmthits'])
    _chunk_collect = _chunk_collect.drop(columns=['ntpmthits'])

    ## Separate labels and features
    features=['pmthits_1','pmthits_7']
    labels=['xp_pri','yp_pri']

    ## Split arrays into (random) train and test subsets.
    ## Could also be done with sklearn.model_selection.train_test_split,
    ## but already randomized from simulation (see plots bleow).
    train_label     = _chunk_collect.loc[:int(np.floor(_chunk_collect.shape[0]*file_split_train))-1,labels]
    predict_label   = _chunk_collect.loc[int(np.floor(_chunk_collect.shape[0]*file_split_train)):,labels]
    train_feature   = _chunk_collect.loc[:int(np.floor(_chunk_collect.shape[0]*file_split_train))-1,features[0]:features[1]]
    predict_feature = _chunk_collect.loc[int(np.floor(_chunk_collect.shape[0]*file_split_train)):,features[0]:features[1]]

    del(_chunk_collect)

    ## Convert to numpy arrays
    train_feature   = train_feature.to_numpy()
    train_label     = train_label.to_numpy()
    predict_feature = predict_feature.to_numpy()
    predict_label   = predict_label.to_numpy()

    ## Normalize labels to [-0.5, 0.5] to make network easier to train 
    ## as using smaller, centered values is often better.
    ## Have to rescale later.
    scaling_factor = 70
    train_label = train_label/scaling_factor
    predict_label = predict_label/scaling_factor
    
    ## Return
    return train_feature, train_label, predict_feature, predict_label

In [3]:
#############################################
## Optimizing the NN
#############################################

def create_model(train_feature, train_label, predict_feature, predict_label):
    """
    Model providing function:

    Create Keras model with double curly brackets dropped-in as needed.
    Return value has to be a valid python dictionary with two customary keys:
        - loss: Specify a numeric evaluation metric to be minimized
        - status: Just use STATUS_OK and see hyperopt documentation if not feasible
    The last one is optional, though recommended, namely:
        - model: specify the model just created so that we can later use it again.
    """
    
    ## Building the Model
    pmts = int(7) # number of PMTs
    
    model = Sequential()
    model.add(Dense(64, input_shape=(pmts,)))
    model.add(Activation('relu'))
    #model.add(Dropout(0.1))
    model.add(Dense(64))
    model.add(Activation('relu'))
    #model.add(Dropout(0.1))
    model.add(Dense(2))  # x and y
    model.add(Activation('linear'))
    
    ## Compiling the Model
    model.compile(optimizer={{choice(['rmsprop', 'adam', 'sgd'])}}, # {{choice(['rmsprop', 'adam', 'sgd'])}} -> 'adam'
                  loss='mean_squared_error',
                  metrics=['mean_squared_error']
             )
    
    ## Training the Model
    result = model.fit(train_feature, train_label,
                       epochs=30,
                       batch_size=128,
                       validation_split=0.2,
                       verbose=1
                      )
    
    ## Get the lowest validation loss of the training epochs
    validation_loss = np.amin(result.history['val_loss']) 
    print('Best validation loss of epoch:', validation_loss)
    return {'loss': validation_loss, 'status': STATUS_OK, 'model': model}

In [4]:
best_run, best_model = optim.minimize(model=create_model,
                                      data=data,
                                      algo=tpe.suggest,
                                      max_evals=5,
                                      trials=Trials(),
                                      #verbose = True,
                                      eval_space = True,
                                      notebook_name='XeBRA_Position_Reconstruction_Optimize_NN' # This is important!
                                     )
X_train, Y_train, X_test, Y_test = data()
print("Evalutation of best performing model:")
print(best_model.evaluate(X_test, Y_test))
print("Best performing model chosen hyper-parameters:")
print(best_run)

best_model.save('best_model.h5')

>>> Imports:
#coding=utf-8

from __future__ import print_function

try:
    import numpy as np
except:
    pass

try:
    from hyperopt import Trials, STATUS_OK, tpe
except:
    pass

try:
    from keras.datasets import mnist
except:
    pass

try:
    from keras.layers.core import Dense, Dropout, Activation
except:
    pass

try:
    from keras.models import Sequential
except:
    pass

try:
    from keras.utils import np_utils
except:
    pass

try:
    from keras.optimizers import SGD, Adam
except:
    pass

try:
    from hyperas import optim
except:
    pass

try:
    from hyperas.distributions import choice, uniform
except:
    pass

try:
    import glob
except:
    pass

try:
    import uproot
except:
    pass

try:
    import pandas as pd
except:
    pass

try:
    import concurrent.futures
except:
    pass

>>> Hyperas search space:

def get_space():
    return {
        'optimizer': hp.choice('optimizer', ['rmsprop', 'adam', 'sgd']),
    }

>>> Data
   1: 
   2: """
   3: Data


W0808 16:49:16.536515 140534868752192 deprecation_wrapper.py:119] From /home/alex/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.


W0808 16:49:16.554147 140534868752192 deprecation_wrapper.py:119] From /home/alex/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.


W0808 16:49:16.556869 140534868752192 deprecation_wrapper.py:119] From /home/alex/anaconda3/lib/python3.7/site-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.


W0808 16:49:16.604652 140534868752192 deprecation_wrapper.py:119] From /home/alex/anaconda3/lib/python3.7/site-packages/keras/optimizers.py:790: The name tf.train.Optimizer is deprecated. Please use tf.compat.v1.train.Optimizer instead.


W0808 16:49

Train on 720000 samples, validate on 180000 samples
Epoch 1/30                                         
   128/720000 [..............................]     
 - ETA: 18:43 - loss: 0.0586 - mean_squared_error: 0.0586
                                                   
  4608/720000 [..............................]     
 - ETA: 38s - loss: 0.0586 - mean_squared_error: 0.0586  
                                                   
  8704/720000 [..............................]     
 - ETA: 24s - loss: 0.0568 - mean_squared_error: 0.0568
                                                   
 12416/720000 [..............................]     
 - ETA: 19s - loss: 0.0549 - mean_squared_error: 0.0549
                                                   
 17152/720000 [..............................]     
 - ETA: 16s - loss: 0.0530 - mean_squared_error: 0.0530
                                                   
 21120/720000 [..............................]     
 - ETA: 14s - loss: 0.0514 - mean_square

                                                  
223488/720000 [========>.....................]     
 - ETA: 6s - loss: 0.0173 - mean_squared_error: 0.0173
                                                  
227968/720000 [========>.....................]     
 - ETA: 6s - loss: 0.0170 - mean_squared_error: 0.0170
                                                  
232576/720000 [========>.....................]     
 - ETA: 6s - loss: 0.0167 - mean_squared_error: 0.0167
                                                  
237440/720000 [========>.....................]     
 - ETA: 5s - loss: 0.0164 - mean_squared_error: 0.0164
                                                  
241664/720000 [=========>....................]     
 - ETA: 5s - loss: 0.0162 - mean_squared_error: 0.0162
                                                  
246656/720000 [=========>....................]     
 - ETA: 5s - loss: 0.0159 - mean_squared_error: 0.0159
                                                  
2

 - ETA: 3s - loss: 0.0095 - mean_squared_error: 0.0095
                                                  
453120/720000 [=================>............]     
 - ETA: 3s - loss: 0.0095 - mean_squared_error: 0.0095
                                                  
457600/720000 [==================>...........]     
 - ETA: 3s - loss: 0.0094 - mean_squared_error: 0.0094
                                                  
462208/720000 [==================>...........]     
 - ETA: 3s - loss: 0.0093 - mean_squared_error: 0.0093
                                                  
466304/720000 [==================>...........]     
 - ETA: 3s - loss: 0.0092 - mean_squared_error: 0.0092
                                                  
470656/720000 [==================>...........]     
 - ETA: 2s - loss: 0.0092 - mean_squared_error: 0.0092
                                                  
475264/720000 [==================>...........]     
 - ETA: 2s - loss: 0.0091 - mean_squared_error: 0.00

...

 - ETA: 7s - loss: 3.8807e-04 - mean_squared_error: 3.8807e-04                   
                                                                                
 62080/720000 [=>............................]                                   
 - ETA: 7s - loss: 3.8846e-04 - mean_squared_error: 3.8846e-04                   
                                                                                
 67200/720000 [=>............................]                                   
 - ETA: 7s - loss: 3.8789e-04 - mean_squared_error: 3.8789e-04                   
                                                                                
 72064/720000 [==>...........................]                                   
 - ETA: 7s - loss: 3.8805e-04 - mean_squared_error: 3.8805e-04                   
                                                                                
 76672/720000 [==>...........................]                                   
 - ETA: 7s - loss: 3

                                                                                
219904/720000 [========>.....................]                                   
 - ETA: 5s - loss: 3.8815e-04 - mean_squared_error: 3.8815e-04                   
                                                                                
224640/720000 [========>.....................]                                   
 - ETA: 5s - loss: 3.8765e-04 - mean_squared_error: 3.8765e-04                   
                                                                                
229632/720000 [========>.....................]                                   
 - ETA: 5s - loss: 3.8813e-04 - mean_squared_error: 3.8813e-04                   
                                                                                
234368/720000 [========>.....................]                                   
 - ETA: 5s - loss: 3.8804e-04 - mean_squared_error: 3.8804e-04                   
                    

379136/720000 [==============>...............]                                   
 - ETA: 3s - loss: 3.8742e-04 - mean_squared_error: 3.8742e-04                   
                                                                                
383744/720000 [==============>...............]                                   
 - ETA: 3s - loss: 3.8740e-04 - mean_squared_error: 3.8740e-04                   
                                                                                
388352/720000 [===============>..............]                                   
 - ETA: 3s - loss: 3.8726e-04 - mean_squared_error: 3.8726e-04                   
                                                                                
393088/720000 [===============>..............]                                   
 - ETA: 3s - loss: 3.8721e-04 - mean_squared_error: 3.8721e-04                   
                                                                                
397440/720000 [=====

 - ETA: 1s - loss: 3.8779e-04 - mean_squared_error: 3.8779e-04                   
                                                                                
539008/720000 [=====================>........]                                   
 - ETA: 1s - loss: 3.8786e-04 - mean_squared_error: 3.8786e-04                   
                                                                                
543616/720000 [=====================>........]                                   
 - ETA: 1s - loss: 3.8786e-04 - mean_squared_error: 3.8786e-04                   
                                                                                
547584/720000 [=====================>........]                                   
 - ETA: 1s - loss: 3.8788e-04 - mean_squared_error: 3.8788e-04                   
                                                                                
552576/720000 [======================>.......]                                   
 - ETA: 1s - loss: 3

                                                                                
694400/720000 [===========================>..]                                   
 - ETA: 0s - loss: 3.8774e-04 - mean_squared_error: 3.8774e-04                   
                                                                                
699008/720000 [============================>.]                                   
 - ETA: 0s - loss: 3.8785e-04 - mean_squared_error: 3.8785e-04                   
                                                                                
703872/720000 [============================>.]                                   
 - ETA: 0s - loss: 3.8770e-04 - mean_squared_error: 3.8770e-04                   
                                                                                
708608/720000 [============================>.]                                   
 - ETA: 0s - loss: 3.8778e-04 - mean_squared_error: 3.8778e-04                   
                    